In [ ]:
%matplotlib inline


# Example for exterior penalty applied to the Sobieski test case.


This section describes how to set up and solve the MDO problem relative to the
`Sobieski test case <sobieski_problem>` with |g| applying external penalty.

.. seealso::

   To start with a simpler MDO problem, and for a detailed description
   of how to plug a test case into |g|, see `sellar_mdo`.



## Solving with an `MDF formulation <mdf_formulation>`

In this example, we solve the range optimization using the following
`MDF formulation <mdf_formulation>`:

- The `MDF formulation <mdf_formulation>` couples all the disciplines
  during the `mda` at each optimization iteration.
- All the :term:`design variables` are equally treated, concatenated in a
  single vector and given to a single :term:`optimization algorithm` as the
  unknowns of the problem.
- There is no specific :term:`constraint` due to the `MDF formulation
  <mdf_formulation>`.
- Only the design :term:`constraints` $g\_1$, $g\_2$ and
  $g\_3$ are added to the problem.
- The :term:`objective function` is the range (the $y\_4$ variable in
  the model), computed after the `mda`.

## Imports
All the imports needed for the tutorials are performed here.



In [ ]:
from __future__ import annotations

from gemseo.api import configure_logger
from gemseo.api import create_discipline
from gemseo.api import create_scenario
from gemseo.api import get_available_formulations
from gemseo.disciplines.utils import get_all_inputs
from gemseo.disciplines.utils import get_all_outputs
from gemseo.problems.sobieski.core.problem import SobieskiProblem

configure_logger()

## Step 1: Creation of :class:`.MDODiscipline`

To build the scenario, we first instantiate the disciplines. Here, the
disciplines themselves have already been
developed and interfaced with |g| (see `benchmark_problems`).



In [ ]:
disciplines = create_discipline(
    [
        "SobieskiPropulsion",
        "SobieskiAerodynamics",
        "SobieskiMission",
        "SobieskiStructure",
    ]
)

.. tip::

   For the disciplines that are not interfaced with |g|, the |g|'s
   :mod:`~gemseo.api` eases the creation of disciplines without having
   to import them.

   See `api`.



## Step 2: Creation of :class:`.Scenario`

The scenario delegates the creation of the optimization problem to the
`MDO formulation <mdo_formulations>`.

Therefore, it needs the list of :code:`disciplines`, the names of the formulation,
the name of the objective function and the design space.

- The :code:`design_space` (shown below for reference)
  defines the unknowns of the optimization problem, and their bounds. It contains
  all the design variables needed by the `MDF formulation <mdf_formulation>`.
  It can be imported from a text file, or created from scratch with the methods
  :meth:`~gemseo.api.create_design_space` and
  :meth:`~gemseo.algos.design_space.DesignSpace.add_variable`. In this case,
  we will retrieve it from the ``SobieskiProblem`` already defined in |g|.



In [ ]:
design_space = SobieskiProblem().design_space
x_0 = design_space.get_current_value(as_dict=True)

.. code::


          name      lower_bound      value      upper_bound  type
          x_shared      0.01          0.05          0.09     float
          x_shared    30000.0       45000.0       60000.0    float
          x_shared      1.4           1.6           1.8      float
          x_shared      2.5           5.5           8.5      float
          x_shared      40.0          55.0          70.0     float
          x_shared     500.0         1000.0        1500.0    float
          x_1           0.1           0.25          0.4      float
          x_1           0.75          1.0           1.25     float
          x_2           0.75          1.0           1.25     float
          x_3           0.1           0.5           1.0      float
          y_14        24850.0    50606.9741711    77100.0    float
          y_14        -7700.0    7306.20262124    45000.0    float
          y_32         0.235       0.50279625      0.795     float
          y_31         2960.0    6354.32430691    10185.0    float
          y_24          0.44       4.15006276      11.13     float
          y_34          0.44       1.10754577       1.98     float
          y_23         3365.0    12194.2671934    26400.0    float
          y_21        24850.0    50606.9741711    77250.0    float
          y_12        24850.0      50606.9742     77250.0    float
          y_12          0.45          0.95          1.5      float

- The available `MDO formulations <mdo_formulations>` are located in the
  **gemseo.formulations** package, see `extending-gemseo` for extending
  GEMSEO with other formulations.
- The :code:`formulation` classname (here, :code:`"MDF"`) shall be passed to
  the scenario to select them.
- The list of available formulations can be obtained by using
  :meth:`~gemseo.api.get_available_formulations`.



In [ ]:
get_available_formulations()

- $y\_4$ corresponds to the :code:`objective_name`. This name must be one
  of the disciplines outputs, here the ``SobieskiMission`` discipline. The list of
  all outputs of the disciplines can be obtained by using
  :meth:`~gemseo.disciplines.utils.get_all_outputs`:



In [ ]:
get_all_outputs(disciplines)
get_all_inputs(disciplines)

From these :class:`~gemseo.core.discipline.MDODiscipline`, design space,
`MDO formulation <mdo_formulations>` name and objective function name,
we build the scenario:



In [ ]:
scenario = create_scenario(
    disciplines,
    formulation="MDF",
    maximize_objective=True,
    objective_name="y_4",
    design_space=design_space,
)

The range function ($y\_4$) should be maximized. However, optimizers
minimize functions by default. Which is why, when creating the scenario, the argument
:code:`maximize_objective` shall be set to :code:`True`.

### Differentiation method

We may choose the way derivatives are computed:


**Function derivatives.** As analytical disciplinary derivatives are
available for the Sobieski test-case, they can be used instead of computing
the derivatives with finite-differences or with the complex-step method.
The easiest way to set a method is to let the optimizer determine it:



In [ ]:
scenario.set_differentiation_method()

The default behavior of the optimizer triggers :term:`finite differences`.
It corresponds to:

.. code::

  scenario.set_differentiation_method("finite_differences",1e-7)

It it also possible to differentiate functions by means of the
:term:`complex step` method:

.. code::

  scenario.set_differentiation_method("complex_step",1e-30j)

### Constraints

Similarly to the objective function, the constraints names are a subset
of the disciplines' outputs. They can be obtained by using
:meth:`~gemseo.disciplines.utils.get_all_outputs`.

The formulation has a powerful feature to automatically dispatch the constraints
($g\_1, g\_2, g\_3$) and plug them to the optimizers depending on
the formulation. To do that, we use the method
:meth:`~gemseo.core.scenario.Scenario.add_constraint`:



In [ ]:
for constraint in ["g_1", "g_2", "g_3"]:
    scenario.add_constraint(constraint, "ineq")

## Step 3: Apply the exterior penalty and execute the scenario



In [ ]:
scenario.formulation.opt_problem.apply_exterior_penalty(
    objective_scale=10.0, scale_inequality=10.0
)

In this way the L-BFGS-B algorithm can be used to solve the optimization problem.
Note that this algorithm is not suited for constrained optimization problems.



In [ ]:
algo_args = {"max_iter": 10, "algo": "L-BFGS-B"}
scenario.execute(algo_args)

### Post-processing options
To visualize the optimization history of the constraint violation one can use the
:class:`.BasicHistory`:



In [ ]:
scenario.post_process(
    "BasicHistory", variable_names=["g_1", "g_2", "g_3"], save=False, show=True
)

This solution is almost feasible.
The solution can better approximate the original problem solution increasing the value
 of `objective_scale` and  `scale_inequality` parameters.
Step 4: Rerun the scenario with increased penalty and objective scaling.
------------------------------------------------------------------------



In [ ]:
design_space.set_current_value(x_0)
scenario_2 = create_scenario(
    disciplines,
    formulation="MDF",
    maximize_objective=True,
    objective_name="y_4",
    design_space=design_space,
)
for constraint in ["g_1", "g_2", "g_3"]:
    scenario_2.add_constraint(constraint, "ineq")
scenario_2.set_differentiation_method()
scenario_2.formulation.opt_problem.apply_exterior_penalty(
    objective_scale=1000.0, scale_inequality=1000.0
)
algo_args_2 = {"max_iter": 1000, "algo": "L-BFGS-B"}
scenario_2.execute(algo_args_2)
scenario_2.post_process("BasicHistory", variable_names=["-y_4"], save=False, show=True)
scenario_2.post_process(
    "BasicHistory", variable_names=["g_1", "g_2", "g_3"], save=False, show=True
)

The solution feasibility was improved but this comes with a much higher number of
iterations.

